FILE			: main.ipynb
PROJECT			: Shaolin AI Assignment 2
PROGRAMMER		: Jack parkinson
FIRST VERSION	: 2024-Mar-24
DESCRIPTION		:
	This file reads in data from two .CSV files and cross-references them to create a report, then analyzes that report. Both the report and the analysis are output as .txt files.

	The PySteak.py file was included with the assignment (for context, I guess?) but I did not use it. I am including it here for posterity.

Assumptions:
- The instructions state to create a PySteak folder, and a main.ipynb file within both the root and PySteak folders. There is no mention of the PySteak folder or its .ipynb file elsewhere in the instructions. (Perhaps it's meant to hold the analysis? But that's only an estimation on my part.)
- The instructions say to save a sales item's quantity and menu item ID as seprate variables, but only the sales item ID is needed to check the presence of a sales item in the report. The quantity is not used as its own variable.
- The exact formatting of the error message does not work with the way I have made the for-loops, but the meaning is still the same.
- The loop that involves copying values to the final report could probably be organized better and have some logic exported to a function, but that would only a handful of lines of code.
- The instructions for data analysis mention calculating the most profitable menu item with the date and amount, but the exact date is not needed to determine this (profitability = revenue/time).
- The above is true for the most costly menu item.

Program flow:
- Read in CSV data for Menu and Sales into list objects.

- Create a report dict to hold data for each thing on the menu. The report's keys will be unique strings like "spicy miso ramen" and each value being a dict.
	- The second layer dict's KVPs will be count, revenue, cost, profit

- For each sale row, save its description string as a separate variable and check if that's already in the report.
	- If not, add an entry to the report with count/revenue/cost/profit defaulted to 0.

- If the sales item and menu item match, calculate the count/revenue/cost/profit for the sale row. Sum these values with the existing values in the report.
	- If they don't match, output an error message.

- Write out the contents of the report to a text file.

- Analyze the report, then write the analysis to a text file.


In [61]:
# Import statements and set file paths
import csv
from pathlib import Path

menu_filepath = Path("./PySteak/Resources/menu_data.csv")
sales_filepath = Path("./PySteak/Resources/sales_data.csv")

In [62]:
# Lists to hold menu and sales entries
menu = []
sales = []

with open(menu_filepath) as menu_file:
    menu_data = csv.reader(menu_file, delimiter=",")
    menu_header = next(menu_data)
    for row in menu_data:
        menu.append(row)
print("Menu headers: ")
print(menu_header)
print(menu[0])

with open(sales_filepath) as sales_file:
    sales_data = csv.reader(sales_file, delimiter=",")
    sales_header = next(sales_data)
    for row in sales_data:
        sales.append(row)
print("Sales headers: ")
print(sales_header)
print(sales[0])


Menu headers: 
['item', 'category', 'description', 'price', 'cost']
['edamame', 'appetizers', 'boiled soybeans, maldon sea salt', '4', '1']
Sales headers: 
['Line_Item_ID', 'Date', 'Credit_Card_Number', 'Quantity', 'Menu_Item']
['1', '01-01-2017', '7437926611570799', '1', 'spicy miso ramen']


In [63]:
# Store aggregated results for each product in a dict.
# Each report will contain: "01-count", "02-revenue", "03-cost", "04-profit" in a dict.

# Create empty dict of dicts.
restaurant_report = {}

# Save each sale row's item name ("spicy miso ramen") and quantity (4)
for sale in sales:
    sale_name = sale[4]
    menu_item_quantity = float(sale[3])
    # If it isn't in the report, initialize entry and copy values from menu list.
    if sale_name not in restaurant_report:
        restaurant_report[sale_name] = {"01-count": 0, "02-revenue": 0, "03-cost": 0, "04-profit": 0}
        found_menu_data = False
        for menu_item in menu:
            if sale_name == menu_item[0]:
                print("Menu data found for " + sale_name + "; initializing in report")
                # Copy menu item values for price and cost
                menu_item_price = float(menu_item[3])
                menu_item_cost = float(menu_item[4])
                menu_item_profit = menu_item_price - menu_item_cost
                # Add the values from the sale to the final report
                restaurant_report[sale_name]["01-count"] += menu_item_quantity
                restaurant_report[sale_name]["02-revenue"] += (menu_item_quantity * menu_item_price)
                restaurant_report[sale_name]["03-cost"] += (menu_item_quantity * menu_item_cost)
                restaurant_report[sale_name]["04-profit"] += (menu_item_quantity * menu_item_profit)
                found_menu_data = True
        # If you couldn't find proper menu data, output an error message
        if not found_menu_data:
            print(sale_name + " has NO MATCH on the menu!")
    
    # If it's already in the report, just copy the values.
    elif sale_name in restaurant_report:
        found_menu_data = False
        for menu_item in menu:
            if sale_name == menu_item[0]:
                print("Menu data found for " + sale_name + "; adding financial data to report")
                # Copy menu item values for price and cost
                menu_item_price = int(menu_item[3])
                menu_item_cost = int(menu_item[4])
                menu_item_profit = menu_item_price - menu_item_cost
                # Add the values from the sale to the final report
                restaurant_report[sale_name]["01-count"] += menu_item_quantity
                restaurant_report[sale_name]["02-revenue"] += (menu_item_quantity * menu_item_price)
                restaurant_report[sale_name]["03-cost"] += (menu_item_quantity * menu_item_cost)
                restaurant_report[sale_name]["04-profit"] += (menu_item_quantity * menu_item_profit)
                found_menu_data = True
        # If you couldn't find proper menu data, output an error message
        if not found_menu_data:
            print(sale_name + " has NO MATCH on the menu!")

Menu data found for spicy miso ramen; initializing in report
Menu data found for spicy miso ramen; adding financial data to report
Menu data found for tori paitan ramen; initializing in report
Menu data found for tori paitan ramen; adding financial data to report
Menu data found for truffle butter ramen; initializing in report
Menu data found for truffle butter ramen; adding financial data to report
Menu data found for tonkotsu ramen; initializing in report
Menu data found for tonkotsu ramen; adding financial data to report
Menu data found for vegetarian spicy miso; initializing in report
Menu data found for vegetarian spicy miso; adding financial data to report
Menu data found for shio ramen; initializing in report
Menu data found for shio ramen; adding financial data to report
Menu data found for tori paitan ramen; adding financial data to report
Menu data found for tori paitan ramen; adding financial data to report
Menu data found for vegetarian spicy miso; adding financial data to 

In [64]:
# Data Analysis

# Calculate the number of months in the sales data. Assumes the data is ordered in the CSV by date from earliest to latest sale.
restaurant_analysis = {
    "single_most_profitable": [],
    "single_most_costly": [],
    "total_months": 0,
}

first_year = sales[0][1].split("-")[2]
first_month = sales[0][1].split("-")[0]
final_year = sales[-1][1].split("-")[2]
final_month = sales[-1][1].split("-")[0]

total_years = int(final_year) - int(first_year)
total_months = 1 + (int(final_month) - int(first_month)) + (total_years * 12)
restaurant_analysis["total_months"] = total_months

In [65]:
# Calculate the highest single profit for a menu item and the highest single cost for a menu item
most_costly = {
    "item_name": "",
    "total_cost": 0.0
}
most_profitable = {
    "item_name": "",
    "total_profit": 0.0
}

for report_item in restaurant_report:
    if most_costly["item_name"] == "" and most_costly["total_cost"] == 0.0:
        most_costly["item_name"] = report_item
        most_costly["total_cost"] = restaurant_report[report_item]["03-cost"]
    elif most_costly["total_cost"] < restaurant_report[report_item]["03-cost"]:
        most_costly["item_name"] = report_item
        most_costly["total_cost"] = restaurant_report[report_item]["03-cost"]

    if most_profitable["item_name"] == "" and most_profitable["total_profit"] == 0.0:
        most_profitable["item_name"] = report_item
        most_profitable["total_profit"] = restaurant_report[report_item]["04-profit"]
    elif most_profitable["total_profit"] < restaurant_report[report_item]["04-profit"]:
        most_profitable["item_name"] = report_item
        most_profitable["total_profit"] = restaurant_report[report_item]["04-profit"]

In [66]:
# Write contents of the report to a text file.
f = open("restaurant_report.txt", "w")
f.write(str(restaurant_report))
f.close()

# Print analysis and store it to a text file
cost_and_price = "The most costly item to sell is " + most_costly["item_name"] + " with a total cost of " + str(most_costly["total_cost"]) + ". The most profitable item to sell is " + most_profitable["item_name"] + " with a total profit of " + str(most_profitable["total_profit"]) + "."

f = open("restaurant_analysis.txt", "w")
f.write(cost_and_price)
f.close()